In [0]:
# ### DOWNCASTING MEMORY!!!!!! JUST IN CASE 

# # Downcast in order to save memory
# def downcast(df):
#     cols = df.dtypes.index.tolist()
#     types = df.dtypes.values.tolist()
#     for i, t in enumerate(types):
#         # Integer
#         if 'int' in str(t):
#             # Check if minimum and maximum are in the limit of int8
#             if df[cols[i]].min() > np.iinfo(np.int8).min and df[cols[i]].max() < np.iinfo(np.int8).max:
#                 df[cols[i]] = df[cols[i]].astype(np.int8)
#             # Check if minimum and maximum are in the limit of int16
#             elif df[cols[i]].min() > np.iinfo(np.int16).min and df[cols[i]].max() < np.iinfo(np.int16).max:
#                 df[cols[i]] = df[cols[i]].astype(np.int16)
#             # Check if minimum and maximum are in the limit of int32
#             elif df[cols[i]].min() > np.iinfo(np.int32).min and df[cols[i]].max() < np.iinfo(np.int32).max:
#                 df[cols[i]] = df[cols[i]].astype(np.int32)
#             # Choose int64
#             else:
#                 df[cols[i]] = df[cols[i]].astype(np.int64)
#         # Float
#         elif 'float' in str(t):
#             if df[cols[i]].min() > np.finfo(np.float16).min and df[cols[i]].max() < np.finfo(np.float16).max:
#                 df[cols[i]] = df[cols[i]].astype(np.float16)
#             elif df[cols[i]].min() > np.finfo(np.float32).min and df[cols[i]].max() < np.finfo(np.float32).max:
#                 df[cols[i]] = df[cols[i]].astype(np.float32)
#             else:
#                 df[cols[i]] = df[cols[i]].astype(np.float64)
#         # Object
#         elif t == np.object:
#             if cols[i] == 'ds':
#                 df[cols[i]] = pd.to_datetime(df[cols[i]], format='%Y-%m-%d')
#             else:
#                 df[cols[i]] = df[cols[i]].astype('category')
#     return df


# # # Apply downcasting
# df_target_01 = downcast(df)

# # reduces data from 61307 MB to 3100 MB

In [0]:
# IMPORTING DATA ANALYSIS AND VISUALIZATION LIBRARIES
import pandas as pd
from datetime import datetime
pd.set_option('display.max_columns', None)
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

# SPARK LIBRARIES 
import pyspark.sql.functions as F
from pyspark.sql.types import DoubleType
from pyspark.sql.types import IntegerType
from pyspark.sql.types import StringType
from pyspark.sql.types import DoubleType
from pyspark.sql import SparkSession
from pyspark.sql.functions import col, udf
from pyspark.ml.clustering import KMeans
from pyspark.ml.linalg import Vectors
from pyspark.ml.feature import MinMaxScaler, VectorAssembler, StandardScaler
from pyspark.ml.feature import StringIndexer, OneHotEncoder
from pyspark.ml import Pipeline

# MODELING 
# from prophet import Prophet
import logging
from sklearn.metrics import mean_squared_error, mean_absolute_error
from sklearn.cluster import KMeans
from sklearn import preprocessing
from sklearn.preprocessing import StandardScaler
from sklearn.datasets import make_blobs

# WARNINGS AND LOGISTICS 
#   Make sure we do not get line breaks when doing show on wide dataframes
from IPython.core.display import HTML
display(HTML("<style>pre { white-space: pre !important; }</style>"))
import warnings
warnings.filterwarnings("ignore")
#   disable informational messages from prophet
logging.getLogger('py4j').setLevel(logging.ERROR)



In [0]:
%run ./Snowflake_Connection

In [0]:
sfdt = SnowflakeDataTool()

In [0]:
gl_demand = spark.table('ltf_db.LTF_GOLDEN_LAYER')


In [0]:
gl_features_00 = spark.table('sales_db.LTF_features_query')

In [0]:
corr_00 = demand_df.withColumn('WEEKLY_DEMAND', F.col('WEEKLY_DEMAND').cast(DoubleType()))
corr_01 = corr_00.select('YEAR', 'WEEK', 'DATE', 'CUSTOMER_ID', 'MATERIAL_ID', 'WEEKLY_DEMAND').orderBy('DATE')

In [0]:
# FILTER DATASET INTO INDIVIDUAL YEARS AND CONVERT TO PANDAS TO BE PIVOTTED IN THE NEXT CELL 

corr_01_2019 = corr_01.filter((corr_01.YEAR == '2019')).orderBy('DATE').toPandas()
corr_01_2020 = corr_01.filter((corr_01.YEAR == '2020')).orderBy('DATE').toPandas()
corr_01_2021 = corr_01.filter((corr_01.YEAR == '2021')).orderBy('DATE').toPandas()
corr_01_2022 = corr_01.filter((corr_01.YEAR == '2022')).orderBy('DATE').toPandas()
corr_01_2023 = corr_01.filter((corr_01.YEAR == '2023')).orderBy('DATE').toPandas()

In [0]:
# PIVOT THE FOUR YEARS OF DATA INTO CONCATENATED YEAR / WEEK COLUMNS CONTAINING WEEKLY DEMAND 

import datetime

df_list = [corr_01_2019, corr_01_2020, corr_01_2021, corr_01_2022]
start_year = 2019
df_merged = pd.DataFrame()
# year = str(int(str(df["YEAR"].iloc[0])) + i)
for i, df in enumerate(df_list):
    year = start_year + i
    df = df.pivot_table(index=["CUSTOMER_ID", "MATERIAL_ID"], columns="WEEK", values="WEEKLY_DEMAND")
    df.columns = [f"{year}_week_{col}" for col in df.columns]
    df_merged = pd.concat([df_merged, df], axis=1)
    df_merged_00 = df_merged.fillna(0)

df_merged_01 = df_merged_00.reset_index()
df_merged_01['ID'] = df_merged_01['CUSTOMER_ID'].astype(str) + '_' + df_merged_01['MATERIAL_ID'].astype(str)
df_k_means = df_merged_01
df_k_means_ID = df_merged_01[["CUSTOMER_ID", "MATERIAL_ID", "ID"]]

df_k_means

CUSTOMER_ID 
 MATERIAL_ID 
 2019_week_01 
 2019_week_02 
 2019_week_03 
 2019_week_04 
 2019_week_05 
 2019_week_06 
 2019_week_07 
 2019_week_08 
 2019_week_09 
 2019_week_10 
 2019_week_11 
 2019_week_12 
 2019_week_13 
 2019_week_14 
 2019_week_15 
 2019_week_16 
 2019_week_17 
 2019_week_18 
 2019_week_19 
 2019_week_20 
 2019_week_21 
 2019_week_22 
 2019_week_23 
 2019_week_24 
 2019_week_25 
 2019_week_26 
 2019_week_27 
 2019_week_28 
 2019_week_29 
 2019_week_30 
 2019_week_31 
 2019_week_32 
 2019_week_33 
 2019_week_34 
 2019_week_35 
 2019_week_36 
 2019_week_37 
 2019_week_38 
 2019_week_39 
 2019_week_40 
 2019_week_41 
 2019_week_42 
 2019_week_43 
 2019_week_44 
 2019_week_45 
 2019_week_46 
 2019_week_47 
 2019_week_48 
 2019_week_49 
 2019_week_50 
 2019_week_51 
 2019_week_52 
 2020_week_01 
 2020_week_02 
 2020_week_03 
 2020_week_04 
 2020_week_05 
 2020_week_06 
 2020_week_07 
 2020_week_08 
 2020_week_09 
 2020_week_10 
 2020_week_11 
 2020_week_12 
 2020_week_13 
 2020_week_14 
 2020_week_15 
 2020_week_16 
 2020_week_17 
 2020_week_18 
 2020_week_19 
 2020_week_20 
 2020_week_21 
 2020_week_22 
 2020_week_23 
 2020_week_24 
 2020_week_25 
 2020_week_26 
 2020_week_27 
 2020_week_28 
 2020_week_29 
 2020_week_30 
 2020_week_31 
 2020_week_32 
 2020_week_33 
 2020_week_34 
 2020_week_35 
 2020_week_36 
 2020_week_37 
 2020_week_38 
 2020_week_39 
 2020_week_40 
 2020_week_41 
 2020_week_42 
 2020_week_43 
 2020_week_44 
 2020_week_45 
 2020_week_46 
 2020_week_47 
 2020_week_48 
 2020_week_49 
 2020_week_50 
 2020_week_51 
 2020_week_52 
 2021_week_01 
 2021_week_02 
 2021_week_03 
 2021_week_04 
 2021_week_05 
 2021_week_06 
 2021_week_07 
 2021_week_08 
 2021_week_09 
 2021_week_10 
 2021_week_11 
 2021_week_12 
 2021_week_13 
 2021_week_14 
 2021_week_15 
 2021_week_16 
 2021_week_17 
 2021_week_18 
 2021_week_19 
 2021_week_20 
 2021_week_21 
 2021_week_22 
 2021_week_23 
 2021_week_24 
 2021_week_25 
 2021_week_26 
 2021_week_27 
 2021_week_28 
 2021_week_29 
 2021_week_30 
 2021_week_31 
 2021_week_32 
 2021_week_33 
 2021_week_34 
 2021_week_35 
 2021_week_36 
 2021_week_37 
 2021_week_38 
 2021_week_39 
 2021_week_40 
 2021_week_41 
 2021_week_42 
 2021_week_43 
 2021_week_44 
 2021_week_45 
 2021_week_46 
 2021_week_47 
 2021_week_48 
 2021_week_49 
 2021_week_50 
 2021_week_51 
 2021_week_52 
 2022_week_01 
 2022_week_02 
 2022_week_03 
 2022_week_04 
 2022_week_05 
 2022_week_06 
 2022_week_07 
 2022_week_08 
 2022_week_09 
 2022_week_10 
 2022_week_11 
 2022_week_12 
 2022_week_13 
 2022_week_14 
 2022_week_15 
 2022_week_16 
 2022_week_17 
 2022_week_18 
 2022_week_19 
 2022_week_20 
 2022_week_21 
 2022_week_22 
 2022_week_23 
 2022_week_24 
 2022_week_25 
 2022_week_26 
 2022_week_27 
 2022_week_28 
 2022_week_29 
 2022_week_30 
 2022_week_31 
 2022_week_32 
 2022_week_33 
 2022_week_34 
 2022_week_35 
 2022_week_36 
 2022_week_37 
 2022_week_38 
 2022_week_39 
 2022_week_40 
 2022_week_41 
 2022_week_42 
 2022_week_43 
 2022_week_44 
 2022_week_45 
 2022_week_46 
 2022_week_47 
 2022_week_48 
 2022_week_49 
 2022_week_50 
 2022_week_51 
 2022_week_52 
 ID 
 
 
 
 
 0 
 0500246183 
 000000000000115583 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0

In [0]:
# COUNT NON-ZERO VALUES IN EACH COLUMN 

# nonzero_counts = (df_merged_00.astype(bool).sum())
# nonzero_counts

Out[14]: 2019_week_01     91927
2019_week_02    132625
2019_week_03    134909
2019_week_04    129547
2019_week_05    142910
                 ...  
2022_week_48    172232
2022_week_49    169472
2022_week_50    167093
2022_week_51    160554
2022_week_52    139144
Length: 208, dtype: int64

In [0]:
# NORMALIZATION OF THE DATA THAT ARE FLOAT VALUES 

num_cols = df_k_means.select_dtypes(include= ['int64', 'float64']).columns
norm_data_pd = df_k_means[num_cols].div(df_k_means[num_cols].sum(axis=1), axis=0)
norm_id_data = pd.concat([df_k_means_ID, norm_data_pd], axis = 1, join = 'inner')

norm_id_data

CUSTOMER_ID 
 MATERIAL_ID 
 ID 
 2019_week_01 
 2019_week_02 
 2019_week_03 
 2019_week_04 
 2019_week_05 
 2019_week_06 
 2019_week_07 
 2019_week_08 
 2019_week_09 
 2019_week_10 
 2019_week_11 
 2019_week_12 
 2019_week_13 
 2019_week_14 
 2019_week_15 
 2019_week_16 
 2019_week_17 
 2019_week_18 
 2019_week_19 
 2019_week_20 
 2019_week_21 
 2019_week_22 
 2019_week_23 
 2019_week_24 
 2019_week_25 
 2019_week_26 
 2019_week_27 
 2019_week_28 
 2019_week_29 
 2019_week_30 
 2019_week_31 
 2019_week_32 
 2019_week_33 
 2019_week_34 
 2019_week_35 
 2019_week_36 
 2019_week_37 
 2019_week_38 
 2019_week_39 
 2019_week_40 
 2019_week_41 
 2019_week_42 
 2019_week_43 
 2019_week_44 
 2019_week_45 
 2019_week_46 
 2019_week_47 
 2019_week_48 
 2019_week_49 
 2019_week_50 
 2019_week_51 
 2019_week_52 
 2020_week_01 
 2020_week_02 
 2020_week_03 
 2020_week_04 
 2020_week_05 
 2020_week_06 
 2020_week_07 
 2020_week_08 
 2020_week_09 
 2020_week_10 
 2020_week_11 
 2020_week_12 
 2020_week_13 
 2020_week_14 
 2020_week_15 
 2020_week_16 
 2020_week_17 
 2020_week_18 
 2020_week_19 
 2020_week_20 
 2020_week_21 
 2020_week_22 
 2020_week_23 
 2020_week_24 
 2020_week_25 
 2020_week_26 
 2020_week_27 
 2020_week_28 
 2020_week_29 
 2020_week_30 
 2020_week_31 
 2020_week_32 
 2020_week_33 
 2020_week_34 
 2020_week_35 
 2020_week_36 
 2020_week_37 
 2020_week_38 
 2020_week_39 
 2020_week_40 
 2020_week_41 
 2020_week_42 
 2020_week_43 
 2020_week_44 
 2020_week_45 
 2020_week_46 
 2020_week_47 
 2020_week_48 
 2020_week_49 
 2020_week_50 
 2020_week_51 
 2020_week_52 
 2021_week_01 
 2021_week_02 
 2021_week_03 
 2021_week_04 
 2021_week_05 
 2021_week_06 
 2021_week_07 
 2021_week_08 
 2021_week_09 
 2021_week_10 
 2021_week_11 
 2021_week_12 
 2021_week_13 
 2021_week_14 
 2021_week_15 
 2021_week_16 
 2021_week_17 
 2021_week_18 
 2021_week_19 
 2021_week_20 
 2021_week_21 
 2021_week_22 
 2021_week_23 
 2021_week_24 
 2021_week_25 
 2021_week_26 
 2021_week_27 
 2021_week_28 
 2021_week_29 
 2021_week_30 
 2021_week_31 
 2021_week_32 
 2021_week_33 
 2021_week_34 
 2021_week_35 
 2021_week_36 
 2021_week_37 
 2021_week_38 
 2021_week_39 
 2021_week_40 
 2021_week_41 
 2021_week_42 
 2021_week_43 
 2021_week_44 
 2021_week_45 
 2021_week_46 
 2021_week_47 
 2021_week_48 
 2021_week_49 
 2021_week_50 
 2021_week_51 
 2021_week_52 
 2022_week_01 
 2022_week_02 
 2022_week_03 
 2022_week_04 
 2022_week_05 
 2022_week_06 
 2022_week_07 
 2022_week_08 
 2022_week_09 
 2022_week_10 
 2022_week_11 
 2022_week_12 
 2022_week_13 
 2022_week_14 
 2022_week_15 
 2022_week_16 
 2022_week_17 
 2022_week_18 
 2022_week_19 
 2022_week_20 
 2022_week_21 
 2022_week_22 
 2022_week_23 
 2022_week_24 
 2022_week_25 
 2022_week_26 
 2022_week_27 
 2022_week_28 
 2022_week_29 
 2022_week_30 
 2022_week_31 
 2022_week_32 
 2022_week_33 
 2022_week_34 
 2022_week_35 
 2022_week_36 
 2022_week_37 
 2022_week_38 
 2022_week_39 
 2022_week_40 
 2022_week_41 
 2022_week_42 
 2022_week_43 
 2022_week_44 
 2022_week_45 
 2022_week_46 
 2022_week_47 
 2022_week_48 
 2022_week_49 
 2022_week_50 
 2022_week_51 
 2022_week_52 
 
 
 
 
 0 
 0500246183 
 000000000000115583 
 0500246183_000000000000115583 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.000000 
 0.000000 
 0.000000 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.000000 
 0.0 
 0.000000 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 0.0 
 

In [0]:
#CHANGING THE PANDAS PIVOT TABLE DATAFRAME INTO A SPARK DATAFRAME TO BE VECTORIZED FOR K MEANS CLUSTERING 

from pyspark.ml.feature import VectorAssembler, StandardScaler
from pyspark.ml.clustering import KMeans

# Convert pandas dataframe to PySpark dataframe
sp_norm = spark.createDataFrame(norm_id_data)

# Convert to dense vector representation
columns_to_select = [c for c in sp_norm.columns if c.startswith("20")]
assembler = VectorAssembler(inputCols=columns_to_select, outputCol="features")
df_vectorized = assembler.transform(sp_norm)

display(df_vectorized)

CUSTOMER_ID MATERIAL_ID ID 2019_week_01 2019_week_02 2019_week_03 2019_week_04 2019_week_05 2019_week_06 2019_week_07 2019_week_08 2019_week_09 2019_week_10 2019_week_11 2019_week_12 2019_week_13 2019_week_14 2019_week_15 2019_week_16 2019_week_17 2019_week_18 2019_week_19 2019_week_20 2019_week_21 2019_week_22 2019_week_23 2019_week_24 2019_week_25 2019_week_26 2019_week_27 2019_week_28 2019_week_29 2019_week_30 2019_week_31 2019_week_32 2019_week_33 2019_week_34 2019_week_35 2019_week_36 2019_week_37 2019_week_38 2019_week_39 2019_week_40 2019_week_41 2019_week_42 2019_week_43 2019_week_44 2019_week_45 2019_week_46 2019_week_47 2019_week_48 2019_week_49 2019_week_50 2019_week_51 2019_week_52 2020_week_01 2020_week_02 2020_week_03 2020_week_04 2020_week_05 2020_week_06 2020_week_07 2020_week_08 2020_week_09 2020_week_10 2020_week_11 2020_week_12 2020_week_13 2020_week_14 2020_week_15 2020_week_16 2020_week_17 2020_week_18 2020_week_19 2020_week_20 2020_week_21 2020_week_22 2020_week_23 2020_week_24 2020_week_25 2020_week_26 2020_week_27 2020_week_28 2020_week_29 2020_week_30 2020_week_31 2020_week_32 2020_week_33 2020_week_34 2020_week_35 2020_week_36 2020_week_37 2020_week_38 2020_week_39 2020_week_40 2020_week_41 2020_week_42 2020_week_43 2020_week_44 2020_week_45 2020_week_46 2020_week_47 2020_week_48 2020_week_49 2020_week_50 2020_week_51 2020_week_52 2021_week_01 2021_week_02 2021_week_03 2021_week_04 2021_week_05 2021_week_06 2021_week_07 2021_week_08 2021_week_09 2021_week_10 2021_week_11 2021_week_12 2021_week_13 2021_week_14 2021_week_15 2021_week_16 2021_week_17 2021_week_18 2021_week_19 2021_week_20 2021_week_21 2021_week_22 2021_week_23 2021_week_24 2021_week_25 2021_week_26 2021_week_27 2021_week_28 2021_week_29 2021_week_30 2021_week_31 2021_week_32 2021_week_33 2021_week_34 2021_week_35 2021_week_36 2021_week_37 2021_week_38 2021_week_39 2021_week_40 2021_week_41 2021_week_42 2021_week_43 2021_week_44 2021_week_45 2021_week_46 2021_week_47 2021_week_48 2021_week_49 2021_week_50 2021_week_51 2021_week_52 2022_week_01 2022_week_02 2022_week_03 2022_week_04 2022_week_05 2022_week_06 2022_week_07 2022_week_08 2022_week_09 2022_week_10 2022_week_11 2022_week_12 2022_week_13 2022_week_14 2022_week_15 2022_week_16 2022_week_17 2022_week_18 2022_week_19 2022_week_20 2022_week_21 2022_week_22 2022_week_23 2022_week_24 2022_week_25 2022_week_26 2022_week_27 2022_week_28 2022_week_29 2022_week_30 2022_week_31 2022_week_32 2022_week_33 2022_week_34 2022_week_35 2022_week_36 2022_week_37 2022_week_38 2022_week_39 2022_week_40 2022_week_41 2022_week_42 2022_week_43 2022_week_44 2022_week_45 2022_week_46 2022_week_47 2022_week_48 2022_week_49 2022_week_50 2022_week_51 2022_week_52 features 0500246183 000000000000115583 0500246183_000000000000115583 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 1.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 Map(vectorType -> sparse, length -> 208, indices -> List(141), values -> List(1.0)) 0500246183 000000000000115586 0500246183_000000000000115586 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 

In [0]:
# USING THE SHAPE OF THE ENTIRE DATASET TO DETERMINE THE NUMBER OF CLUSTERS. THEN PERFORM MODELING USING A PROPER SEED AND TWO SIZE CLUSTERS 

# FIND K VALUE and split data into train and test ---------------------------------------------------------------------------------
kmeans_train_ = df_merged_01[:int(df_merged_01.shape[0]*0.75)]
# test_ = df_merged_01[int(df_merged_01.shape[0]*0.75):]

# rule of thumb in choosing the value of k is k = sqrt(N)/2 or sometimes simply sqrt(N), where N stands for the number of samples/data points in your training dataset. Tip is to use odd number of K so that there is no tie between choosing a class 
k_value = np.sqrt(len(kmeans_train_.index)).astype('int')   # = 916 
k_value_div_2 = (np.sqrt(len(kmeans_train_.index))/2).astype('int')   # = 458 

# Step 3a: Fit k-means model (k = sqrt(N))
# kmeans_916 = KMeans(k=k_value, seed=42)
# kmeans_model_916 = kmeans_916.fit(df_vectorized.select("features"))

# Step 3b: Fit k-means model (k = sqrt(N)/2)
kmeans_458 = KMeans(k=k_value_div_2, seed=42)
kmeans_model_458 = kmeans_458.fit(df_vectorized.select("features"))


In [0]:
# CLUSTER PREDICITON AND SIMPLE EVALUATION OF THE CLUSTERS USING WSSE 

from pyspark.ml.evaluation import ClusteringEvaluator

# step 4 predict the cluster assignment for each data point
df_cluster_pred_458 = kmeans_model_458.transform(df_vectorized) 
# df_cluster_pred_916 = kmeans_model_916.transform(df_vectorized) 


# Step 5a: Compute WSSSE ("Within Set Sum of Squared Error")
evaluator_458 = ClusteringEvaluator()
# evaluator_916 = ClusteringEvaluator()

wssse_458 = evaluator_458.evaluate(df_cluster_pred_458)
# wssse_916 = evaluator_916.evaluate(df_cluster_pred_916)


print("For k = 458, the Within Set Sum of Squared Error = " + str(wssse_458))
# print("For k = 916, the Within Set Sum of Squared Error = " + str(wssse_916))


For k = 458, the Within Set Sum of Squared Error = 0.009289521257983232


In [0]:
# GROUP THE CUSTOMER_ID, MATERIAL_ID, COMBINED_ID, AND CLUSTER_PREDICTION FOR 458 CLUSTER AMOUNT 

pred_result_458 = df_cluster_pred_458.select(df_cluster_pred_458.CUSTOMER_ID.alias('CUS_ID'), df_cluster_pred_458.MATERIAL_ID.alias('MAT_ID'), df_cluster_pred_458.ID.alias('COMB_ID'), df_cluster_pred_458.prediction.alias('CLUSTER_PRED'))

display(pred_result_458)

CUS_ID MAT_ID COMB_ID CLUSTER_PRED 0500246183 000000000000115583 0500246183_000000000000115583 4 0500246183 000000000000115586 0500246183_000000000000115586 4 0500246183 000000000000116149 0500246183_000000000000116149 4 0500246183 000000000000116366 0500246183_000000000000116366 279 0500246183 000000000000117603 0500246183_000000000000117603 4 0500246186 000000000000115583 0500246186_000000000000115583 428 0500246189 000000000000101728 0500246189_000000000000101728 330 0500246189 000000000000101891 0500246189_000000000000101891 297 0500246189 000000000000102603 0500246189_000000000000102603 300 0500246189 000000000000102748 0500246189_000000000000102748 399 0500246189 000000000000102752 0500246189_000000000000102752 300 0500246189 000000000000103029 0500246189_000000000000103029 261 0500246189 000000000000117635 0500246189_000000000000117635 72 0500246189 000000000000117641 0500246189_000000000000117641 297 0500246189 000000000000117803 0500246189_000000000000117803 261 0500246189 000000000000119826 0500246189_000000000000119826 261 0500246189 000000000000119827 0500246189_000000000000119827 396 0500246189 000000000000125622 0500246189_000000000000125622 52 0500246189 000000000000125623 0500246189_000000000000125623 261 0500246189 000000000000125624 0500246189_000000000000125624 261 0500246189 000000000000125625 0500246189_000000000000125625 261 0500246453 000000000000101891 0500246453_000000000000101891 323 0500246453 000000000000102580 0500246453_000000000000102580 219 0500246453 000000000000102603 0500246453_000000000000102603 323 0500246453 000000000000102604 0500246453_000000000000102604 323 0500246453 000000000000102605 0500246453_000000000000102605 323 0500246453 000000000000103029 0500246453_000000000000103029 27 0500246453 000000000000112309 0500246453_000000000000112309 85 0500246453 000000000000114756 0500246453_000000000000114756 13 0500246453 000000000000117635 0500246453_000000000000117635 323 0500246453 000000000000117803 0500246453_000000000000117803 27 0500246453 000000000000119826 0500246453_000000000000119826 205 0500246453 000000000000119827 0500246453_000000000000119827 436 0500246453 000000000000135333 0500246453_000000000000135333 363 0500246454 000000000000102439 0500246454_000000000000102439 359 0500246454 000000000000102604 0500246454_000000000000102604 323 0500246454 000000000000112259 0500246454_000000000000112259 436 0500246454 000000000000112309 0500246454_000000000000112309 275 0500246454 000000000000115304 0500246454_000000000000115304 48 0500246454 000000000000117641 0500246454_000000000000117641 270 0500246454 000000000000117808 0500246454_000000000000117808 123 0500246454 000000000000119790 0500246454_000000000000119790 323 0500246454 000000000000119827 0500246454_000000000000119827 436 0500246454 000000000000120461 0500246454_000000000000120461 378 0500246454 000000000000121024 0500246454_000000000000121024 418 0500246454 000000000000121751 0500246454_000000000000121751 3 0500246454 000000000000121765 0500246454_000000000000121765 378 0500246454 000000000000121964 0500246454_000000000000121964 323 0500246454 000000000000125492 0500246454_000000000000125492 436 0500246454 000000000000125522 0500246454_000000000000125522 3 0500246454 000000000000125622 0500246454_000000000000125622 42 0500246454 000000000000129254 0500246454_000000000000129254 141 0500246454 000000000000130471 0500246454_000000000000130471 270 0500246454 000000000000135333 0500246454_000000000000135333 363 0500246454 000000000000137799 0500246454_000000000000137799 378 0500246454 000000000000156089 0500246454_000000000000156089 219 0500246454 000000000000156090 0500246454_000000000000156090 123 0500246454 000000000000156110 0500246454_000000000000156110 141 0500246454 000000000000156120 0500246454_000000000000156120 257 0500246454 000000000000156122 0500246454_000000000000156122 257 0500246454 000000000000157121 0500246454_000000000000157121 257 0500246454 000000000000157347 0500246454_000000000000157347 123 0500246454 000000

In [0]:
# *** USING DIFFERENT K // GROUP THE CUSTOMER_ID, MATERIAL_ID, COMBINED_ID, AND CLUSTER_PREDICTION FOR 916 CLUSTER AMOUNT 


pred_result_916 = df_cluster_pred_916.select(df_cluster_pred_916.CUSTOMER_ID.alias('CUS_ID'), df_cluster_pred_916.MATERIAL_ID.alias('MAT_ID'), df_cluster_pred_916.ID.alias('COMB_ID'), df_cluster_pred_916.prediction.alias('CLUSTER_PRED'))

display(pred_result_916)

CUS_ID MAT_ID COMB_ID CLUSTER_PRED 0500246183 000000000000115583 0500246183_000000000000115583 582 0500246183 000000000000115586 0500246183_000000000000115586 582 0500246183 000000000000116149 0500246183_000000000000116149 582 0500246183 000000000000116366 0500246183_000000000000116366 799 0500246183 000000000000117603 0500246183_000000000000117603 582 0500246186 000000000000115583 0500246186_000000000000115583 95 0500246189 000000000000101728 0500246189_000000000000101728 261 0500246189 000000000000101891 0500246189_000000000000101891 730 0500246189 000000000000102603 0500246189_000000000000102603 788 0500246189 000000000000102748 0500246189_000000000000102748 901 0500246189 000000000000102752 0500246189_000000000000102752 179 0500246189 000000000000103029 0500246189_000000000000103029 785 0500246189 000000000000117635 0500246189_000000000000117635 788 0500246189 000000000000117641 0500246189_000000000000117641 730 0500246189 000000000000117803 0500246189_000000000000117803 833 0500246189 000000000000119826 0500246189_000000000000119826 785 0500246189 000000000000119827 0500246189_000000000000119827 564 0500246189 000000000000125622 0500246189_000000000000125622 50 0500246189 000000000000125623 0500246189_000000000000125623 69 0500246189 000000000000125624 0500246189_000000000000125624 785 0500246189 000000000000125625 0500246189_000000000000125625 687 0500246453 000000000000101891 0500246453_000000000000101891 889 0500246453 000000000000102580 0500246453_000000000000102580 404 0500246453 000000000000102603 0500246453_000000000000102603 889 0500246453 000000000000102604 0500246453_000000000000102604 889 0500246453 000000000000102605 0500246453_000000000000102605 889 0500246453 000000000000103029 0500246453_000000000000103029 840 0500246453 000000000000112309 0500246453_000000000000112309 405 0500246453 000000000000114756 0500246453_000000000000114756 669 0500246453 000000000000117635 0500246453_000000000000117635 425 0500246453 000000000000117803 0500246453_000000000000117803 840 0500246453 000000000000119826 0500246453_000000000000119826 164 0500246453 000000000000119827 0500246453_000000000000119827 678 0500246453 000000000000135333 0500246453_000000000000135333 685 0500246454 000000000000102439 0500246454_000000000000102439 663 0500246454 000000000000102604 0500246454_000000000000102604 889 0500246454 000000000000112259 0500246454_000000000000112259 551 0500246454 000000000000112309 0500246454_000000000000112309 902 0500246454 000000000000115304 0500246454_000000000000115304 653 0500246454 000000000000117641 0500246454_000000000000117641 626 0500246454 000000000000117808 0500246454_000000000000117808 663 0500246454 000000000000119790 0500246454_000000000000119790 870 0500246454 000000000000119827 0500246454_000000000000119827 505 0500246454 000000000000120461 0500246454_000000000000120461 22 0500246454 000000000000121024 0500246454_000000000000121024 889 0500246454 000000000000121751 0500246454_000000000000121751 870 0500246454 000000000000121765 0500246454_000000000000121765 22 0500246454 000000000000121964 0500246454_000000000000121964 889 0500246454 000000000000125492 0500246454_000000000000125492 678 0500246454 000000000000125522 0500246454_000000000000125522 870 0500246454 000000000000125622 0500246454_000000000000125622 111 0500246454 000000000000129254 0500246454_000000000000129254 553 0500246454 000000000000130471 0500246454_000000000000130471 624 0500246454 000000000000135333 0500246454_000000000000135333 685 0500246454 000000000000137799 0500246454_000000000000137799 626 0500246454 000000000000156089 0500246454_000000000000156089 404 0500246454 000000000000156090 0500246454_000000000000156090 663 0500246454 000000000000156110 0500246454_000000000000156110 553 0500246454 000000000000156120 0500246454_000000000000156120 653 0500246454 000000000000156122 0500246454_000000000000156122 663 0500246454 000000000000157121 0500246454_000000000000157121 879 0500246454 000000000000157347 0500246454_000000000000157347 663 05

JOINING THE PREDICTION RESULTS TO THE ORIGINAL (NOT NORMALIZED) DATASET WITH ACTUAL ORDERS AND THEN SAVING THOSE TABLES

In [0]:
# CLUSTER SUMMARY OF THE ASSIGNMENTS PER CLUSTER, UNIQUE CUSTOMER_ID AND UNIQUE MATERIAL_ID PER CLUSTER FOR 458

cluster_summary_458_001 = pred_result_458.groupBy("CLUSTER_PRED").agg(
    F.count("*").alias("assignments_per_cluster"),
    F.countDistinct("CUS_ID").alias("unique_customer_id_per_cluster"),
    F.countDistinct("MAT_ID").alias("unique_material_id_per_cluster")
).orderBy('CLUSTER_PRED')

display(cluster_summary_458_001)
cluster_summary_458_001.write.mode('overwrite').saveAsTable('sales_db.cluster_summary_unique_ID_458_clusters')


CLUSTER_PRED assignments_per_cluster unique_customer_id_per_cluster unique_material_id_per_cluster 0 139367 6310 593 1 1592 963 418 2 570 343 302 3 1228 816 368 4 652 406 285 5 641 414 303 6 929 512 323 7 1112 733 372 8 344 200 237 9 1340 895 399 10 974 610 332 11 652 416 224 12 1011 667 288 13 556 351 262 14 1467 986 378 15 485 362 253 16 828 341 213 17 1351 934 398 18 7313 2597 564 19 1146 765 157 20 1362 926 406 21 655 429 259 22 1302 848 343 23 372 223 248 24 3911 2131 522 25 481 299 267 26 1796 1120 424 27 2753 1578 490 28 723 458 325 29 1387 893 260 30 360 249 219 31 1754 989 441 32 587 406 290 33 543 377 229 34 4818 2221 511 35 1072 585 200 36 1657 942 403 37 1169 761 374 38 2442 1495 447 39 1358 809 385 40 2015 1183 462 41 565 380 297 42 771 515 290 43 28822 3757 628 44 970 401 319 45 1971 1105 449 46 723 448 253 47 1225 853 384 48 2677 1549 471 49 787 522 325 50 25901 3289 571 51 409 290 223 52 4961 2064 564 53 488 281 284 54 675 457 322 55 2689 1599 468 56 1636 959 334 57 1366 790 341 58 1362 820 369 59 425 216 265 60 1737 1129 421 61 426 309 181 62 1003 651 360 63 736 496 284 64 1089 666 363 65 1130 747 288 66 1000 722 328 67 3192 1786 475 68 1085 667 382 69 442 278 254 70 1973 1165 365 71 3229 1720 435 72 828 608 319 73 665 420 272 74 2707 1560 472 75 1181 777 347 76 498 327 275 77 527 258 258 78 725 332 232 79 572 364 246 80 1048 623 339 81 1245 889 371 82 1127 778 373 83 726 471 320 84 2210 1180 489 85 336 237 202 86 287 207 115 87 1122 723 358 88 541 392 196 89 849 563 235 90 1580 1041 419 91 413 290 249 92 337 225 225 93 529 332 280 94 604 413 279 95 2808 941 320 96 327 215 221 97 1305 867 350 98 544 342 283 99 1012 679 344 100 1683 1082 384 101 584 367 298 102 1132 803 384 103 430 269 261 104 662 442 210 105 1304 861 367 106 922 526 299 107 417 260 283 108 2068 1290 432 109 632 320 274 110 1459 937 371 111 1039 674 314 112 648 390 185 113 543 370 225 114 1181 768 355 115 705 478 315 116 803 554 307 117 558 332 283 118 1963 1206 408 119 889 631 273 120 1149 773 331 121 738 361 319 122 917 597 341 123 1729 1060 420 124 481 293 270 125 638 416 300 126 531 322 250 127 588 338 310 128 437 268 239 129 553 355 265 130 720 440 326 131 398 265 237 132 1280 831 385 133 1815 941 339 134 1020 662 244 135 586 351 288 136 6068 1547 500 137 620 377 296 138 1330 818 317 139 293 182 202 140 1888 1116 408 141 952 643 354 142 1047 567 248 143 620 347 309 144 333 255 182 145 1438 883 421 146 378 236 218 147 855 529 235 148 358 213 240 149 5754 2575 504 150 340 200 186 151 546 370 241 152 1952 1230 425 153 1403 926 403 154 425 292 224 155 694 462 258 156 621 348 284 157 505 332 257 158 358 244 226 159 648 422 281 160 1472 879 420 161 1545 1033 392 162 641 429 218 163 413 288 208 164 2599 1501 459 165 1055 631 276 166 540 302 246 167 1556 1015 413 168 1335 771 391 169 555 396 274 170 369 224 243 171 475 293 235 172 646 435 292 173 5446 2300 519 174 1249 682 449 175 1245 793 361 176 1151 775 397 177 3435 1877 482 178 861 530 351 179 398 234 263 180 1228 808 368 181 1060 661 264 182 386 267 240 183 587 329 322 184 360 242 227 185 1560 866 417 186 1119 750 292 187 854 643 265 188 428 259 249 189 666 449 247 190 812 486 198 191 3047 1669 463 192 1205 729 377 193 1663 1003 444 194 943 609 279 195 1193 707 355 196 526 300 276 197 366 271 157 198 583 326 249 199 2779 1554 469 200 454 295 243 201 357 240 212 202 5170 2461 511 203 1817 1169 440 204 1156 805 367 205 976 629 275 206 565 364 273 207 1531 867 387 208 1167 798 378 209 3268 1719 496 210 455 253 273 211 522 310 295 212 1056 631 225 213 986 653 328 214 1482 889 372 215 1099 678 260 216 841 587 240 217 442 278 221 218 761 433 240 219 1419 918 371 220 1052 594 212 221 3636 1556 481 222 556 372 238 223 547 373 268 224 1281 822 358 225 544 309 159 226 2614 1481 463 227 381 294 210 228 454 332 201 229 1423 973 376 230 908 618 329 231 663 430 201 232 563 362 237 233 1333 883 361 234 912 591 238 235 502 285 273 236 398 275 235 237 1613 985 443 238 857 463 310 239 2490 1438 441 240 969 625

Output can only be rendered in Databricks

In [0]:
display(cluster_summary_458_002.filter(cluster_summary_458_002.CLUSTER_PRED == 0).select('YEAR', 'WEEK').distinct())


YEAR WEEK 2021 39 2019 49 2020 33 2021 20 2022 15 2019 32 2022 45 2021 35 2020 11 2022 11 2020 10 2020 29 2019 33 2019 38 2021 33 2020 26 2019 04 2019 40 2019 20 2020 28 2019 36 2021 10 2022 48 2020 47 2020 48 2020 22 2021 50 2022 08 2021 31 2022 33 2020 21 2021 09 2023 02 2020 52 2022 38 2021 41 2021 49 2020 15 2019 52 2019 09 2022 19 2020 20 2022 23 2019 07 2022 18 2019 11 2021 28 2019 39 2021 52 2019 30 2021 07 2019 08 2022 32 2019 46 2020 03 2022 09 2022 06 2020 19 2022 07 2021 25 2019 48 2020 36 2019 16 2020 24 2022 46 2019 50 2022 12 2021 47 2021 21 2022 20 2021 15 2021 27 2022 42 2021 46 2021 24 2020 40 2022 01 2021 16 2022 49 2020 50 2020 38 2021 29 2020 27 2021 02 2019 29 2019 21 2022 27 2021 04 2021 34 2020 05 2019 51 2019 47 2022 34 2022 02 2020 07 2020 06 2022 16 2021 51 2021 36 2021 19 2021 11 2021 17 2019 35 2020 34 2019 12 2019 44 2019 41 2021 48 2019 25 2019 22 2021 08 2020 12 2019 10 2021 01 2020 14 2019 43 2022 44 2022 17 2021 05 2019 31 2023 01 2020 01 2021 45 2020 13 2021 42 2022 10 2019 18 2021 43 2021 12 2021 44 2021 18 2020 18 2021 13 2022 35 2022 25 2022 28 2022 52 2022 41 2020 37 2021 26 2019 37 2020 17 2019 14 2022 43 2019 03 2022 24 2020 46 2019 19 2020 39 2022 47 2020 02 2019 01 2019 06 2020 31 2019 15 2023 03 2022 37 2019 17 2019 45 2020 04 2019 42 2020 44 2022 50 2023 04 2022 26 2020 23 2021 22 2022 04 2019 34 2021 03 2021 14 2019 26 2021 06 2019 05 2020 25 2022 14 2019 24 2020 35 2020 08 2020 32 2020 16 2019 13 2020 09 2020 51 2020 43 2022 21 2020 49 2022 05 2022 22 2022 29 2020 42 2022 51 2022 39 2022 03 2019 27 2021 32 2021 38 2020 30 2022 30 2021 30 2022 40 2022 13 2019 02 2020 41 2021 37 2020 45 2022 31 2019 28 2022 36 2019 23 2021 40 2021 23

In [0]:
# *** CLUSTER NUMBER DIFF /// CLUSTER SUMMARY OF THE ASSIGNMENTS PER CLUSTER, UNIQUE CUSTOMER_ID AND UNIQUE MATERIAL_ID PER CLUSTER FOR 916
#

cluster_summary_916_001 = pred_result_916.groupBy("CLUSTER_PRED").agg(
    F.count("*").alias("assignments_per_cluster"),
    F.countDistinct("CUS_ID").alias("unique_customer_id_per_cluster"),
    F.countDistinct("MAT_ID").alias("unique_material_id_per_cluster")
).orderBy('CLUSTER_PRED')

display(cluster_summary_916_001)
cluster_summary_916_001.write.mode('overwrite').saveAsTable('sales_db.cluster_summary_unique_ID_916_clusters')

CLUSTER_PRED assignments_per_cluster unique_customer_id_per_cluster unique_material_id_per_cluster 0 81843 5320 488 1 810 458 288 2 352 231 230 3 646 396 271 4 834 517 230 5 480 339 246 6 520 331 262 7 1278 832 373 8 2835 1664 467 9 1061 779 348 10 380 236 233 11 1420 837 373 12 910 594 340 13 322 228 195 14 233 169 119 15 816 545 270 16 3178 1709 432 17 313 256 127 18 2070 1291 432 19 574 444 236 20 179 131 108 21 2140 1190 443 22 922 625 346 23 1311 543 174 24 182 158 135 25 798 582 315 26 540 338 239 27 264 190 189 28 828 341 213 29 1946 1230 425 30 1423 983 384 31 276 185 188 32 314 219 204 33 837 601 265 34 365 232 231 35 1381 809 386 36 372 252 210 37 526 342 273 38 590 334 278 39 527 370 263 40 231 198 117 41 185 161 140 42 1003 551 243 43 606 392 299 44 586 405 290 45 366 278 190 46 1103 720 356 47 389 253 203 48 585 408 272 49 409 281 212 50 4263 1965 523 51 2046 1208 440 52 1753 1146 424 53 700 440 246 54 1268 746 393 55 1058 783 362 56 1303 881 376 57 166 121 132 58 490 346 149 59 411 249 236 60 293 177 210 61 197 160 138 62 530 351 263 63 915 696 321 64 644 458 260 65 871 599 299 66 1526 1004 351 67 392 323 196 68 626 429 317 69 2398 1519 413 70 654 259 291 71 1330 770 389 72 832 498 199 73 263 172 175 74 837 560 234 75 821 633 326 76 261 205 155 77 2290 1299 248 78 3798 1529 339 79 334 230 210 80 728 461 243 81 526 386 198 82 1087 665 363 83 419 240 244 84 1128 746 287 85 1038 598 305 86 201 165 138 87 989 551 180 88 300 184 216 89 429 265 238 90 305 238 136 91 180 152 112 92 1012 674 328 93 364 236 229 94 324 226 96 95 514 360 250 96 652 405 256 97 427 300 259 98 1842 1196 420 99 627 410 195 100 546 360 280 101 715 511 315 102 750 440 268 103 655 384 310 104 2437 1493 446 105 193 160 126 106 307 250 121 107 483 343 273 108 436 263 260 109 1156 749 374 110 700 487 305 111 756 507 290 112 859 584 286 113 539 359 226 114 242 157 129 115 1833 1159 418 116 303 219 166 117 552 416 240 118 528 303 236 119 275 177 192 120 641 436 271 121 271 164 184 122 663 450 286 123 638 427 218 124 367 229 237 125 439 286 249 126 476 359 248 127 841 539 210 128 761 555 315 129 664 443 210 130 265 215 158 131 6348 2112 476 132 5269 1899 430 133 212 179 119 134 563 403 291 135 543 288 255 136 721 546 312 137 594 380 290 138 1195 723 376 139 190 152 113 140 830 578 100 141 658 444 245 142 564 378 127 143 457 233 280 144 378 257 237 145 1201 840 340 146 638 438 292 147 229 182 115 148 259 202 128 149 403 247 222 150 1167 579 279 151 495 347 210 152 416 213 263 153 625 465 294 154 476 291 266 155 934 629 291 156 534 377 262 157 655 506 290 158 966 714 338 159 326 251 181 160 1250 795 361 161 404 337 230 162 436 294 241 163 497 349 256 164 778 541 226 165 723 466 215 166 350 211 225 167 276 232 166 168 527 384 220 169 642 460 228 170 617 368 287 171 452 274 267 172 471 326 242 173 340 246 163 174 2996 1616 479 175 965 399 317 176 197 170 131 177 1437 973 375 178 515 254 255 179 1078 754 299 180 582 349 288 181 406 225 256 182 634 300 302 183 336 220 243 184 702 464 328 185 1232 798 388 186 4143 2000 514 187 129 102 89 188 897 513 271 189 736 338 235 190 628 319 272 191 1071 718 384 192 519 360 270 193 659 461 294 194 363 235 182 195 419 278 234 196 604 409 252 197 351 237 191 198 564 363 273 199 267 178 45 200 273 221 128 201 612 249 319 202 655 482 295 203 629 441 256 204 210 143 160 205 633 451 283 206 645 484 242 207 467 350 211 208 1246 890 374 209 862 548 294 210 564 357 244 211 513 393 259 212 233 178 144 213 1716 1107 418 214 657 516 276 215 221 164 171 216 700 529 304 217 3092 1747 473 218 600 427 297 219 189 147 124 220 575 397 292 221 197 160 144 222 926 628 355 223 812 563 312 224 672 455 303 225 5088 2316 492 226 236 195 159 227 226 164 123 228 3997 1200 452 229 646 441 308 230 430 283 245 231 326 274 138 232 7622 1948 459 233 2663 1405 460 234 416 321 234 235 887 565 239 236 1408 945 371 237 254 167 120 238 744 523 310 239 571 391 295 240 612 438 295 241 297 176 204 242 15088 2809 502 243 393 301 113 244 1746 1016 432 245 451 2

Output can only be rendered in Databricks

In [0]:
# CLUSTER_SUMMARY # 2 THAT CONTAINS THE MIN, MAX, MEAN, STD OF EACH CLUSTER  *** 458 CLUSTERS ***

# week_cols = [col for col in df_cluster_pred_00.columns if "_week_" in col]

cluster_summary_458_002 = kmeans_prediction_data_join_458.groupBy("CLUSTER_PRED", 'YEAR', 'WEEK').agg(F.round(sum("WEEKLY_DEMAND"), 3).alias("SUM_WEEKLY_DEMAND"),
                            F.min("WEEKLY_DEMAND").alias("MIN_WEEKLY_DEMAND"),
                            F.percentile_approx("WEEKLY_DEMAND", 0.5).alias("MEDIAN_WEEKLY_DEMAND"), \
                            F.max("WEEKLY_DEMAND").alias("MAX_WEEKLY_DEMAND"),
                            F.round(mean("WEEKLY_DEMAND"), 3).alias("MEAN_WEEKLY_DEMAND"), \
                            F.round(F.stddev("WEEKLY_DEMAND"), 3).alias("STANDARD_DEVIATION_WEEKLY_DEMAND")) \
                            .orderBy('CLUSTER_PRED', 'YEAR', 'WEEK')

display(cluster_summary_458_002)
cluster_summary_458_002.write.mode('overwrite').option("overwriteSchema", "true").saveAsTable('sales_db.cluster_stat_summary_458')

#cluster 681 contains over 250 MILLION sum or orders


---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
<command-3653637396065865> in <cell line: 5>()
      3 # week_cols = [col for col in df_cluster_pred_00.columns if "_week_" in col]
      4 
----> 5 cluster_summary_458_002 = kmeans_prediction_data_join_458.groupBy("CLUSTER_PRED", 'YEAR', 'WEEK').agg(F.round(sum("WEEKLY_DEMAND"), 3).alias("SUM_WEEKLY_DEMAND"),
      6                             F.min("WEEKLY_DEMAND").alias("MIN_WEEKLY_DEMAND"),
      7                             F.percentile_approx("WEEKLY_DEMAND", 0.5).alias("MEDIAN_WEEKLY_DEMAND"), \

NameError: name 'kmeans_prediction_data_join_458' is not defined

In [0]:
# CLUSTER_SUMMARY # 2 THAT CONTAINS THE MIN, MAX, MEAN, STD OF EACH CLUSTER  *** 916 CLUSTERS ***


# week_cols = [col for col in df_cluster_pred_00.columns if "_week_" in col]

cluster_summary_916_002 = kmeans_prediction_data_join_916.groupBy("CLUSTER_PRED", 'YEAR', 'WEEK').agg(F.round(sum("WEEKLY_DEMAND"), 3).alias("SUM_WEEKLY_DEMAND"),
                                                        F.min("WEEKLY_DEMAND").alias("MIN_WEEKLY_DEMAND"),
                                                        F.percentile_approx("WEEKLY_DEMAND", 0.5).alias("MEDIAN_WEEKLY_DEMAND"), \
                                                        F.max("WEEKLY_DEMAND").alias("MAX_WEEKLY_DEMAND"),
                                                        F.round(mean("WEEKLY_DEMAND"), 3).alias("MEAN_WEEKLY_DEMAND"), \
                                                        F.round(F.stddev("WEEKLY_DEMAND"), 3).alias("STANDARD_DEVIATION_WEEKLY_DEMAND")) \
                                                        .orderBy('CLUSTER_PRED', 'YEAR', 'WEEK')

display(cluster_summary_916_002)
cluster_summary_916_002.write.mode('overwrite').option("overwriteSchema", "true").saveAsTable('sales_db.cluster_stat_summary_916')

#cluster 681 contains over 166 MILLION sum or orders

CLUSTER_PRED YEAR WEEK SUM_WEEKLY_DEMAND MIN_WEEKLY_DEMAND MEDIAN_WEEKLY_DEMAND MAX_WEEKLY_DEMAND MEAN_WEEKLY_DEMAND STANDARD_DEVIATION_WEEKLY_DEMAND 0 2019 01 87745.297 0.041 2.0 1152.0 6.377 36.592 0 2019 02 148100.89 0.041 2.0 980.0 6.884 28.194 0 2019 03 182442.7 0.041 2.0 1120.0 7.835 29.938 0 2019 04 162589.259 0.041 2.0 980.0 7.348 31.754 0 2019 05 223596.976 0.041 2.0 2785.0 9.157 52.41 0 2019 06 167683.692 0.041 2.0 980.0 7.105 28.408 0 2019 07 164508.823 0.041 2.0 1120.0 7.266 29.984 0 2019 08 161699.861 0.041 2.0 1584.0 6.997 35.331 0 2019 09 180966.889 0.041 2.0 980.0 7.687 30.157 0 2019 10 217800.061 0.041 2.0 1260.0 7.77 35.475 0 2019 11 191955.982 0.041 2.0 980.0 6.811 27.095 0 2019 12 226385.29 0.041 2.0 1248.0 7.358 34.155 0 2019 13 252661.647 0.041 2.0 1120.0 7.667 31.192 0 2019 14 240614.746 0.041 2.0 1120.0 7.19 30.802 0 2019 15 263053.52 0.041 2.0 1736.0 7.792 40.357 0 2019 16 324659.082 0.041 2.0 2112.0 9.328 49.908 0 2019 17 226092.399 0.041 2.0 2400.0 6.986 42.787 0 2019 18 291756.968 0.041 2.0 5952.0 8.943 118.488 0 2019 19 276600.401 0.041 2.0 3648.0 8.263 69.768 0 2019 20 260705.573 0.041 2.0 3072.0 7.949 61.476 0 2019 21 383958.184 0.041 2.0 5184.0 10.755 90.828 0 2019 22 204752.913 0.041 2.0 3360.0 6.829 54.601 0 2019 23 343695.829 0.041 2.0 7392.0 10.292 145.121 0 2019 24 332899.829 0.041 2.0 3840.0 9.278 63.525 0 2019 25 350576.189 0.041 2.0 6144.0 9.9 122.367 0 2019 26 467183.824 0.041 2.0 9984.0 13.114 194.906 0 2019 27 300229.391 0.041 2.0 1376.0 8.828 42.704 0 2019 28 265732.329 0.041 2.0 4128.0 7.668 77.252 0 2019 29 227176.464 0.041 2.0 1330.0 6.492 30.787 0 2019 30 267847.854 0.041 2.0 2496.0 7.632 52.584 0 2019 31 243804.167 0.041 2.0 840.0 6.93 28.405 0 2019 32 262450.645 0.041 2.0 840.0 7.002 28.169 0 2019 33 259831.694 0.041 2.0 2660.0 7.173 44.104 0 2019 34 246547.831 0.041 2.0 1470.0 6.808 33.328 0 2019 35 303388.373 0.041 2.0 1400.0 7.993 35.437 0 2019 36 193921.462 0.041 2.0 1820.0 5.698 31.278 0 2019 37 237217.909 0.041 2.0 1260.0 6.48 27.813 0 2019 38 318035.231 0.041 2.0 1536.0 8.677 48.531 0 2019 39 215797.449 0.041 2.0 910.0 5.9 23.905 0 2019 40 234269.042 0.041 2.0 1260.0 6.825 28.031 0 2019 41 229995.543 0.041 2.0 1120.0 6.334 25.011 0 2019 42 221667.293 0.003 2.0 1120.0 6.021 24.746 0 2019 43 254242.274 0.041 2.0 1890.0 7.1 35.672 0 2019 44 248476.032 0.041 2.0 1120.0 6.995 32.369 0 2019 45 236704.218 0.041 2.0 1920.0 6.635 38.478 0 2019 46 232465.115 0.041 2.0 1680.0 6.273 26.908 0 2019 47 415387.206 0.041 2.0 1920.0 10.716 55.692 0 2019 48 288384.491 0.041 2.0 1208.0 8.329 40.527 0 2019 49 196300.257 0.001 2.0 1190.0 6.006 31.693 0 2019 50 238036.475 0.041 2.0 1240.0 6.871 32.0 0 2019 51 355911.235 0.041 2.0 1640.0 9.574 49.314 0 2019 52 516174.29 0.041 3.0 1536.0 10.4 44.546 0 2020 01 52047.163 0.041 1.0 420.0 3.314 12.784 0 2020 02 205976.327 0.041 2.0 840.0 5.904 24.601 0 2020 03 264010.931 0.041 2.0 1632.0 7.223 35.334 0 2020 04 204746.512 0.041 2.0 1260.0 5.889 26.026 0 2020 05 291122.966 0.041 2.0 1045.0 7.083 31.983 0 2020 06 237819.824 0.041 2.0 845.0 5.63 19.598 0 2020 07 302877.309 0.041 2.0 1920.0 6.978 35.411 0 2020 08 296328.202 0.041 2.0 1470.0 6.618 34.828 0 2020 09 254873.457 0.003 2.0 1190.0 5.762 23.891 0 2020 10 342304.58 0.041 2.0 1152.0 7.2 30.915 0 2020 11 421668.81 0.041 2.0 1540.0 8.428 32.967 0 2020 12 633496.46 0.041 2.0 2450.0 11.751 45.685 0 2020 13 318252.625 0.041 2.0 1680.0 7.517 38.145 0 2020 14 255739.804 0.003 2.0 980.0 6.372 24.301 0 2020 15 394840.474 0.041 2.0 2016.0 9.138 40.576 0 2020 16 318023.56 0.041 2.0 840.0 7.287 25.265 0 2020 17 328922.532 0.041 2.0 1190.0 6.886 29.415 0 2020 18 430338.986 0.041 2.0 1470.0 8.259 36.845 0 2020 19 473356.708 0.041 2.0 2496.0 8.383 42.369 0 2020 20 525841.664 0.041 2.0 2689.0 9.219 57.812 0 2020 21 159721.515 0.041 2.0 1470.0 6.487 39.281 0 2020 22 6263.526 0.041 0.708 1120.0 7.519 63.534 0 2020 23 281319.318 0.041 2.0 2240.0 6.81 35.943 0 2020 24 571908.568 0.041 2.0 3936.0 9.4 62.434 0 2020 25 

SAVE FINAL TABLES JOINED WITH ORIGINAL DATA FOR MODELING

In [0]:
# JOINING THE CLUSTER_PREDICTIONS BACK TO THE ORIGINAL DATA - THE SAVED TABLES WILL ALSO BE USED FOR INPUTS TO GARY FOR IMAGES OF K MEANS ** 458 **

kmeans_prediction_data_join_458 = pred_result_458.join(corr_01, \
    on=[corr_01.CUSTOMER_ID == pred_result_458.CUS_ID, corr_01.MATERIAL_ID == pred_result_458.MAT_ID], \
    how='left' \
    ) \
    .select(corr_01.YEAR, corr_01.WEEK, corr_01.DATE, corr_01.CUSTOMER_ID, corr_01.MATERIAL_ID, corr_01.WEEKLY_DEMAND, \
        pred_result_458.CLUSTER_PRED, pred_result_458.COMB_ID \
    )


kmeans_prediction_data_join_458.write.mode('overwrite').saveAsTable('sales_db.descriptive_clustering_summary_input_data_458')
display(kmeans_prediction_data_join_458)

YEAR WEEK DATE CUSTOMER_ID MATERIAL_ID WEEKLY_DEMAND CLUSTER_PRED COMB_ID 2022 44 2022-11-03 0500264326 000000000000103029 0.083 174 0500264326_000000000000103029 2021 32 2021-08-12 0500264326 000000000000103029 0.25 174 0500264326_000000000000103029 2022 49 2022-12-08 0500264326 000000000000103029 0.166 174 0500264326_000000000000103029 2022 07 2022-02-17 0500264326 000000000000103029 0.166 174 0500264326_000000000000103029 2021 50 2021-12-15 0500264326 000000000000103029 0.083 174 0500264326_000000000000103029 2022 41 2022-10-13 0500264326 000000000000103029 0.083 174 0500264326_000000000000103029 2022 19 2022-05-12 0500264326 000000000000103029 0.083 174 0500264326_000000000000103029 2022 17 2022-04-28 0500264326 000000000000103029 0.083 174 0500264326_000000000000103029 2021 22 2021-06-02 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 16 2022-04-20 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 29 2022-07-20 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2022 37 2022-09-14 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 21 2022-05-25 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 36 2021-09-08 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 15 2022-04-13 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 15 2021-04-14 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 03 2021-01-20 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 04 2022-01-26 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 47 2022-11-23 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2021 09 2021-03-03 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2021 24 2021-06-16 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 43 2022-10-26 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 36 2022-09-07 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2020 28 2020-07-08 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2021 13 2021-03-31 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 07 2021-02-17 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2022 07 2022-02-16 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 44 2021-11-03 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 52 2022-12-28 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 12 2022-03-23 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2022 18 2022-05-04 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2020 32 2020-08-05 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 14 2022-04-06 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 49 2022-12-07 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2022 50 2022-12-14 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 37 2021-09-15 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 50 2021-12-15 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2020 50 2020-12-09 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2020 52 2020-12-29 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2021 52 2021-12-29 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2021 21 2021-05-26 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 20 2021-05-19 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2022 20 2022-05-18 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 12 2021-03-24 0500264744 000000000000151775 2.0 0 0500264744_000000000000151775 2020 40 2020-09-30 0500264744 000000000000151775 1.0 0 0500264744_000000000000151775 2021 10 2021-03-10 0500264744 000000000000151775 2.0 0 0500264744_0000

In [0]:
test = spark.table('sales_db.descriptive_clustering_summary_input_data_458')

test_01 = test.filter((test.YEAR == '2021') & (test.WEEK == '14') & (test.MATERIAL_ID == '000000000000151944'))
display(test_01)

YEAR WEEK DATE CUSTOMER_ID MATERIAL_ID WEEKLY_DEMAND CLUSTER_PRED COMB_ID

In [0]:
from pyspark.sql.functions import sum

summed_df = kmeans_prediction_data_join_458.groupBy("CLUSTER_PRED", 'YEAR', "WEEK").agg(F.round(sum("WEEKLY_DEMAND"), 3).alias("SUM_WEEKLY_DEMAND")) \
                                    .orderBy(["CLUSTER_PRED", "YEAR", "WEEK"], ascending=[True, True, True])



display(summed_df)
# cluster_summary_458_002.write.mode('overwrite').option("overwriteSchema", "true").saveAsTable('sales_db.cluster_stat_summary_458')

CLUSTER_PRED YEAR WEEK SUM_WEEKLY_DEMAND 0 2019 01 131159.31 0 2019 02 224716.479 0 2019 03 296680.793 0 2019 04 258259.075 0 2019 05 354654.277 0 2019 06 324944.245 0 2019 07 275591.232 0 2019 08 247960.371 0 2019 09 300853.987 0 2019 10 350401.275 0 2019 11 347906.28 0 2019 12 350581.545 0 2019 13 387549.518 0 2019 14 378580.31 0 2019 15 358422.624 0 2019 16 467196.568 0 2019 17 337301.547 0 2019 18 471421.76 0 2019 19 415124.997 0 2019 20 372978.405 0 2019 21 603759.311 0 2019 22 320607.326 0 2019 23 507520.242 0 2019 24 512632.56 0 2019 25 511361.921 0 2019 26 659510.689 0 2019 27 498561.18 0 2019 28 362302.944 0 2019 29 347073.654 0 2019 30 383893.953 0 2019 31 343670.45 0 2019 32 405580.756 0 2019 33 389255.983 0 2019 34 321676.373 0 2019 35 431756.436 0 2019 36 316691.939 0 2019 37 342083.811 0 2019 38 410008.139 0 2019 39 288992.26 0 2019 40 339786.323 0 2019 41 408443.939 0 2019 42 373879.811 0 2019 43 362246.314 0 2019 44 346508.344 0 2019 45 370723.211 0 2019 46 366734.216 0 2019 47 640883.877 0 2019 48 482656.416 0 2019 49 300520.979 0 2019 50 472338.307 0 2019 51 576187.5 0 2019 52 874433.673 0 2020 01 84797.573 0 2020 02 314305.962 0 2020 03 434662.091 0 2020 04 328509.101 0 2020 05 500857.093 0 2020 06 457001.286 0 2020 07 512107.391 0 2020 08 588985.988 0 2020 09 520944.428 0 2020 10 589444.158 0 2020 11 746032.737 0 2020 12 1130208.197 0 2020 13 519955.206 0 2020 14 536534.401 0 2020 15 810462.407 0 2020 16 665839.566 0 2020 17 621815.0 0 2020 18 829097.593 0 2020 19 1066225.006 0 2020 20 1146916.85 0 2020 21 280103.912 0 2020 22 4697.041 0 2020 23 611997.634 0 2020 24 1005774.193 0 2020 25 1092897.086 0 2020 26 1192181.99 0 2020 27 1302098.959 0 2020 28 860667.444 0 2020 29 1131811.434 0 2020 30 1177177.808 0 2020 31 961207.504 0 2020 32 1082713.406 0 2020 33 1099473.791 0 2020 34 1271226.157 0 2020 35 1204699.847 0 2020 36 1424083.106 0 2020 37 1131723.529 0 2020 38 1198342.169 0 2020 39 1063051.954 0 2020 40 1126780.14 0 2020 41 1303525.749 0 2020 42 1256969.03 0 2020 43 1328999.873 0 2020 44 1174021.624 0 2020 45 1256993.17 0 2020 46 1193906.583 0 2020 47 1775671.474 0 2020 48 1312139.681 0 2020 49 1124208.731 0 2020 50 1176905.125 0 2020 51 1296597.457 0 2020 52 3506702.902 0 2021 01 1197742.594 0 2021 02 1047968.927 0 2021 03 1047506.446 0 2021 04 1511634.712 0 2021 05 1522314.617 0 2021 06 1213820.053 0 2021 07 885529.033 0 2021 08 951673.046 0 2021 09 897344.048 0 2021 10 973792.381 0 2021 11 981627.574 0 2021 12 940099.392 0 2021 13 1149363.567 0 2021 14 1080824.368 0 2021 15 1048697.747 0 2021 16 916945.881 0 2021 17 921250.132 0 2021 18 888756.056 0 2021 19 1158371.758 0 2021 20 1335830.273 0 2021 21 1462295.243 0 2021 22 995134.308 0 2021 23 1201496.196 0 2021 24 1450140.873 0 2021 25 1470163.195 0 2021 26 1471966.369 0 2021 27 1078787.717 0 2021 28 1239207.357 0 2021 29 1006158.695 0 2021 30 962077.008 0 2021 31 865916.753 0 2021 32 1235411.361 0 2021 33 1313438.302 0 2021 34 1200171.535 0 2021 35 1383259.043 0 2021 36 1078188.806 0 2021 37 1179231.285 0 2021 38 1358684.995 0 2021 39 1223942.955 0 2021 40 1142532.497 0 2021 41 1142499.217 0 2021 42 1234099.35 0 2021 43 1278183.512 0 2021 44 1003464.334 0 2021 45 1238740.828 0 2021 46 1492209.348 0 2021 47 1217969.753 0 2021 48 1104025.824 0 2021 49 1110432.543 0 2021 50 1538362.745 0 2021 51 1467636.476 0 2021 52 799926.872 0 2022 01 853337.478 0 2022 02 1139433.984 0 2022 03 907245.621 0 2022 04 1055020.3 0 2022 05 1090922.094 0 2022 06 1248715.416 0 2022 07 1063020.812 0 2022 08 1077440.301 0 2022 09 968680.187 0 2022 10 1080314.6 0 2022 11 1254428.631 0 2022 12 1092806.203 0 2022 13 959475.754 0 2022 14 1105318.732 0 2022 15 1235106.175 0 2022 16 927593.528 0 2022 17 910276.897 0 2022 18 1101403.548 0 2022 19 1037363.259 0 2022 20 1153064.837 0 2022 21 1355422.018 0 2022 22 840785.411 0 2022 23 992719.773 0 2022 24 1129531.31 0 2022 25 1061072.521 0 2022 26 1209901.922 0 2022 27 803224.788 0 2022 28 1006967.492 0 2022 29 997289.311 0 2022 30 10

In [0]:
time_series_transformation = summed_df.withColumn("DATE", make_date(col("YEAR"), lit(1), lit(1))) \
        .withColumn("DATE", date_add(col("DATE"), 6 - dayofweek(col("DATE")))) \
        .withColumn("DATE", date_add(col("DATE"), ((col("WEEK")-1)*7).cast("int"))) \
        .withColumn("DATE", date_sub(col("DATE"), dayofweek(col("DATE"))-1)) \
        .withColumn("DATE", date_add(col("DATE"), 5)).orderBy('CLUSTER_PRED', 'YEAR', 'WEEK')

display(time_series_transformation)
time_series_transformation.write.mode('overwrite').option("overwriteSchema", "true").saveAsTable('sales_db.time_series_ltf_weekly_data_458')


CLUSTER_PRED YEAR WEEK SUM_WEEKLY_DEMAND DATE 0 2019 01 131159.31 2019-01-04 0 2019 02 224716.479 2019-01-11 0 2019 03 296680.793 2019-01-18 0 2019 04 258259.075 2019-01-25 0 2019 05 354654.277 2019-02-01 0 2019 06 324944.245 2019-02-08 0 2019 07 275591.232 2019-02-15 0 2019 08 247960.371 2019-02-22 0 2019 09 300853.987 2019-03-01 0 2019 10 350401.275 2019-03-08 0 2019 11 347906.28 2019-03-15 0 2019 12 350581.545 2019-03-22 0 2019 13 387549.518 2019-03-29 0 2019 14 378580.31 2019-04-05 0 2019 15 358422.624 2019-04-12 0 2019 16 467196.568 2019-04-19 0 2019 17 337301.547 2019-04-26 0 2019 18 471421.76 2019-05-03 0 2019 19 415124.997 2019-05-10 0 2019 20 372978.405 2019-05-17 0 2019 21 603759.311 2019-05-24 0 2019 22 320607.326 2019-05-31 0 2019 23 507520.242 2019-06-07 0 2019 24 512632.56 2019-06-14 0 2019 25 511361.921 2019-06-21 0 2019 26 659510.689 2019-06-28 0 2019 27 498561.18 2019-07-05 0 2019 28 362302.944 2019-07-12 0 2019 29 347073.654 2019-07-19 0 2019 30 383893.953 2019-07-26 0 2019 31 343670.45 2019-08-02 0 2019 32 405580.756 2019-08-09 0 2019 33 389255.983 2019-08-16 0 2019 34 321676.373 2019-08-23 0 2019 35 431756.436 2019-08-30 0 2019 36 316691.939 2019-09-06 0 2019 37 342083.811 2019-09-13 0 2019 38 410008.139 2019-09-20 0 2019 39 288992.26 2019-09-27 0 2019 40 339786.323 2019-10-04 0 2019 41 408443.939 2019-10-11 0 2019 42 373879.811 2019-10-18 0 2019 43 362246.314 2019-10-25 0 2019 44 346508.344 2019-11-01 0 2019 45 370723.211 2019-11-08 0 2019 46 366734.216 2019-11-15 0 2019 47 640883.877 2019-11-22 0 2019 48 482656.416 2019-11-29 0 2019 49 300520.979 2019-12-06 0 2019 50 472338.307 2019-12-13 0 2019 51 576187.5 2019-12-20 0 2019 52 874433.673 2019-12-27 0 2020 01 84797.573 2020-01-03 0 2020 02 314305.962 2020-01-10 0 2020 03 434662.091 2020-01-17 0 2020 04 328509.101 2020-01-24 0 2020 05 500857.093 2020-01-31 0 2020 06 457001.286 2020-02-07 0 2020 07 512107.391 2020-02-14 0 2020 08 588985.988 2020-02-21 0 2020 09 520944.428 2020-02-28 0 2020 10 589444.158 2020-03-06 0 2020 11 746032.737 2020-03-13 0 2020 12 1130208.197 2020-03-20 0 2020 13 519955.206 2020-03-27 0 2020 14 536534.401 2020-04-03 0 2020 15 810462.407 2020-04-10 0 2020 16 665839.566 2020-04-17 0 2020 17 621815.0 2020-04-24 0 2020 18 829097.593 2020-05-01 0 2020 19 1066225.006 2020-05-08 0 2020 20 1146916.85 2020-05-15 0 2020 21 280103.912 2020-05-22 0 2020 22 4697.041 2020-05-29 0 2020 23 611997.634 2020-06-05 0 2020 24 1005774.193 2020-06-12 0 2020 25 1092897.086 2020-06-19 0 2020 26 1192181.99 2020-06-26 0 2020 27 1302098.959 2020-07-03 0 2020 28 860667.444 2020-07-10 0 2020 29 1131811.434 2020-07-17 0 2020 30 1177177.808 2020-07-24 0 2020 31 961207.504 2020-07-31 0 2020 32 1082713.406 2020-08-07 0 2020 33 1099473.791 2020-08-14 0 2020 34 1271226.157 2020-08-21 0 2020 35 1204699.847 2020-08-28 0 2020 36 1424083.106 2020-09-04 0 2020 37 1131723.529 2020-09-11 0 2020 38 1198342.169 2020-09-18 0 2020 39 1063051.954 2020-09-25 0 2020 40 1126780.14 2020-10-02 0 2020 41 1303525.749 2020-10-09 0 2020 42 1256969.03 2020-10-16 0 2020 43 1328999.873 2020-10-23 0 2020 44 1174021.624 2020-10-30 0 2020 45 1256993.17 2020-11-06 0 2020 46 1193906.583 2020-11-13 0 2020 47 1775671.474 2020-11-20 0 2020 48 1312139.681 2020-11-27 0 2020 49 1124208.731 2020-12-04 0 2020 50 1176905.125 2020-12-11 0 2020 51 1296597.457 2020-12-18 0 2020 52 3506702.902 2020-12-25 0 2021 01 1197742.594 2021-01-01 0 2021 02 1047968.927 2021-01-08 0 2021 03 1047506.446 2021-01-15 0 2021 04 1511634.712 2021-01-22 0 2021 05 1522314.617 2021-01-29 0 2021 06 1213820.053 2021-02-05 0 2021 07 885529.033 2021-02-12 0 2021 08 951673.046 2021-02-19 0 2021 09 897344.048 2021-02-26 0 2021 10 973792.381 2021-03-05 0 2021 11 981627.574 2021-03-12 0 2021 12 940099.392 2021-03-19 0 2021 13 1149363.567 2021-03-26 0 2021 14 1080824.368 2021-04-02 0 2021 15 1048697.747 2021-04-09 0 2021 16 916945.881 2021-04-16 0 2021 17 921250.132 2021-04-23 0 2021 18 888756.056 2021-04-30 0 2021 19 1158371.758 2021-05-0

In [0]:
x = spark.table('sales_db.time_series_ltf_weekly_data_458')

display(x.filter((x.YEAR == '2022') & (x.CLUSTER_PRED == '105')))

CLUSTER_PRED YEAR WEEK SUM_WEEKLY_DEMAND DATE 105 2022 01 20.999 2021-12-31 105 2022 02 52.037 2022-01-07 105 2022 03 25.0 2022-01-14 105 2022 04 31.288 2022-01-21 105 2022 05 27.291 2022-01-28 105 2022 06 22.539 2022-02-04 105 2022 07 24.624 2022-02-11 105 2022 08 24.622 2022-02-18 105 2022 09 33.75 2022-02-25 105 2022 10 23.914 2022-03-04 105 2022 11 44.707 2022-03-11 105 2022 12 46.457 2022-03-18 105 2022 13 23.956 2022-03-25 105 2022 14 34.789 2022-04-01 105 2022 15 44.54 2022-04-08 105 2022 16 31.041 2022-04-15 105 2022 17 50.583 2022-04-22 105 2022 18 30.868 2022-04-29 105 2022 19 19.291 2022-05-06 105 2022 20 39.373 2022-05-13 105 2022 21 38.583 2022-05-20 105 2022 22 32.668 2022-05-27 105 2022 23 42.581 2022-06-03 105 2022 24 22.791 2022-06-10 105 2022 25 36.332 2022-06-17 105 2022 26 46.332 2022-06-24 105 2022 27 17.416 2022-07-01 105 2022 28 34.208 2022-07-08 105 2022 29 31.083 2022-07-15 105 2022 30 74.082 2022-07-22 105 2022 31 44.207 2022-07-29 105 2022 32 59.29 2022-08-05 105 2022 33 37.0 2022-08-12 105 2022 34 31.538 2022-08-19 105 2022 35 94.124 2022-08-26 105 2022 36 53.208 2022-09-02 105 2022 37 30.0 2022-09-09 105 2022 38 18.58 2022-09-16 105 2022 39 49.75 2022-09-23 105 2022 40 69.124 2022-09-30 105 2022 41 30.333 2022-10-07 105 2022 42 17.916 2022-10-14 105 2022 43 24.791 2022-10-21 105 2022 44 196.039 2022-10-28 105 2022 45 29.5 2022-11-04 105 2022 46 12.666 2022-11-11 105 2022 47 8.5 2022-11-18 105 2022 48 11.871 2022-11-25 105 2022 49 7.416 2022-12-02 105 2022 50 12.374 2022-12-09 105 2022 51 26.0 2022-12-16 105 2022 52 6.0 2022-12-23

In [0]:
# JOINING THE CLUSTER_PREDICTIONS BACK TO THE ORIGINAL DATA - THE SAVED TABLES WILL ALSO BE USED FOR INPUTS TO GARY FOR IMAGES OF K MEANS ** 916 **

kmeans_prediction_data_join_916 = pred_result_916.join(corr_01, \
    on=[corr_01.CUSTOMER_ID == pred_result_916.CUS_ID, corr_01.MATERIAL_ID == pred_result_916.MAT_ID], \
    how='left' \
    ) \
    .select(corr_01.YEAR, corr_01.WEEK, corr_01.DATE, corr_01.CUSTOMER_ID, corr_01.MATERIAL_ID, corr_01.WEEKLY_DEMAND, \
        pred_result_916.CLUSTER_PRED, pred_result_916.COMB_ID \
    ).orderBy('DATE')


kmeans_prediction_data_join_916.write.mode('overwrite').saveAsTable('sales_db.descriptive_clustering_summary_input_data_916')
display(kmeans_prediction_data_join_916)

YEAR WEEK DATE CUSTOMER_ID MATERIAL_ID WEEKLY_DEMAND CLUSTER_PRED COMB_ID 2019 01 2019-01-01 0600249744 000000000000154812 5.0 343 0600249744_000000000000154812 2019 01 2019-01-01 0600249744 000000000000133251 12.0 519 0600249744_000000000000133251 2019 01 2019-01-01 0600252516 000000000000154845 2.0 628 0600252516_000000000000154845 2019 01 2019-01-01 0600250180 000000000000132895 10.0 519 0600250180_000000000000132895 2019 01 2019-01-01 0600249744 000000000000116662 15.0 519 0600249744_000000000000116662 2019 01 2019-01-01 0600250946 000000000000151477 1.0 85 0600250946_000000000000151477 2019 01 2019-01-01 0600249744 000000000000132551 3.0 681 0600249744_000000000000132551 2019 01 2019-01-01 0600250946 000000000000152196 2.0 0 0600250946_000000000000152196 2019 01 2019-01-01 0600252401 000000000000129252 5.0 681 0600252401_000000000000129252 2019 01 2019-01-01 0600250946 000000000000153142 1.0 556 0600250946_000000000000153142 2019 01 2019-01-01 0600249744 000000000000134402 2.0 635 0600249744_000000000000134402 2019 01 2019-01-01 0600251786 000000000000117603 2.0 519 0600251786_000000000000117603 2019 01 2019-01-01 0600249744 000000000000125623 2.0 712 0600249744_000000000000125623 2019 01 2019-01-01 0600251844 000000000000120461 1.0 519 0600251844_000000000000120461 2019 01 2019-01-01 0600249744 000000000000142720 3.0 681 0600249744_000000000000142720 2019 01 2019-01-01 0600252208 000000000000132606 2.0 681 0600252208_000000000000132606 2019 01 2019-01-01 0600249744 000000000000116320 5.0 519 0600249744_000000000000116320 2019 01 2019-01-01 0600252214 000000000000132529 2.0 681 0600252214_000000000000132529 2019 01 2019-01-01 0600250907 000000000000151224 1.0 844 0600250907_000000000000151224 2019 01 2019-01-01 0600252214 000000000000151793 6.0 519 0600252214_000000000000151793 2019 01 2019-01-01 0600249744 000000000000132529 4.0 681 0600249744_000000000000132529 2019 01 2019-01-01 0600252375 000000000000130468 1.0 628 0600252375_000000000000130468 2019 01 2019-01-01 0600250946 000000000000119826 2.0 0 0600250946_000000000000119826 2019 01 2019-01-01 0600252401 000000000000136907 3.0 681 0600252401_000000000000136907 2019 01 2019-01-01 0600249744 000000000000136907 1.0 681 0600249744_000000000000136907 2019 01 2019-01-01 0600252401 000000000000136907 3.0 681 0600252401_000000000000136907 2019 01 2019-01-01 0600251244 000000000000137763 1.0 628 0600251244_000000000000137763 2019 01 2019-01-01 0600252418 000000000000132541 1.0 519 0600252418_000000000000132541 2019 01 2019-01-01 0600250180 000000000000129093 2.0 885 0600250180_000000000000129093 2019 01 2019-01-01 0600252439 000000000000151757 4.0 519 0600252439_000000000000151757 2019 01 2019-01-01 0600251782 000000000000123372 1.0 628 0600251782_000000000000123372 2019 01 2019-01-01 0600252447 000000000000151988 1.0 519 0600252447_000000000000151988 2019 01 2019-01-01 0600249744 000000000000117603 152.0 681 0600249744_000000000000117603 2019 01 2019-01-01 0600252516 000000000000145160 6.0 276 0600252516_000000000000145160 2019 01 2019-01-01 0600251782 000000000000145967 1.0 628 0600251782_000000000000145967 2019 01 2019-01-01 0600252516 000000000000151779 7.0 635 0600252516_000000000000151779 2019 01 2019-01-01 0600250907 000000000000135333 1.0 423 0600250907_000000000000135333 2019 01 2019-01-01 0600252516 000000000000152922 2.0 744 0600252516_000000000000152922 2019 01 2019-01-01 0600252212 000000000000132531 1.0 681 0600252212_000000000000132531 2019 01 2019-01-01 0600252516 000000000000154810 3.0 242 0600252516_000000000000154810 2019 01 2019-01-01 0600249744 000000000000154850 1.0 903 0600249744_000000000000154850 2019 01 2019-01-01 0600252578 000000000000115586 144.0 681 0600252578_000000000000115586 2019 01 2019-01-01 0600252212 000000000000152965 1.0 635 0600252212_000000000000152965 2019 01 2019-01-01 0600252770 000000000000103503 2.0 681 0600252770_000000000000103503 2019 01 2019-01-01 0600250946 000000000000132606 2.0 681 0600250946_000000000000132606 2019 01 2